## Import libs

In [ ]:
!pip install fedot

In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt
from sklearn.metrics import mean_squared_error, mean_absolute_error
from math import sqrt
import warnings
from fedot.api.main import Fedot
from fedot.core.repository.tasks import Task, TaskTypesEnum
from fedot.core.repository.tasks import TsForecastingParams
from statsmodels.tsa.ar_model import AutoReg
warnings.filterwarnings('ignore')

## Load data

In [2]:
data = pd.read_parquet('data/AllYearsES1.parquet')
data = data[data['Estacao'] == 'Vila Velha - Ibes']
data['datetime'] = pd.to_datetime(data['Data'] + ' ' + data['Hora'], format='mixed', errors='coerce')
data.set_index('datetime', inplace=True)
data = data.sort_index()

In [6]:
data[['Poluente', 'Valor']].groupby(['Poluente']).count()

Valor
Poluente       
CO        68393
MP10      64656
MP2.5     47085
NO         9552
NO2       42648
O3        55188
PTS       26182
SO2       42065

In [3]:
mp_10 = data[data['Poluente'] == 'MP10']
mp_10.head()

Data   Hora            Estacao Codigo Poluente  \
datetime                                                                    
2015-01-01 00:30:00  2015-01-01  00:30  Vila Velha - Ibes   ES07     MP10   
2015-01-01 01:30:00  2015-01-01  01:30  Vila Velha - Ibes   ES07     MP10   
2015-01-01 02:30:00  2015-01-01  02:30  Vila Velha - Ibes   ES07     MP10   
2015-01-01 03:30:00  2015-01-01  03:30  Vila Velha - Ibes   ES07     MP10   
2015-01-01 04:30:00  2015-01-01  04:30  Vila Velha - Ibes   ES07     MP10   

                     Valor Unidade        Tipo  
datetime                                        
2015-01-01 00:30:00   14.0   ug/m3  automatica  
2015-01-01 01:30:00   37.0   ug/m3  automatica  
2015-01-01 02:30:00   23.0   ug/m3  automatica  
2015-01-01 03:30:00   10.0   ug/m3  automatica  
2015-01-01 04:30:00    5.0   ug/m3  automatica

In [8]:
fig = px.line(mp_10, x=mp_10.index, y=['Valor'],
              labels={'value': 'Концентрация (ug/m3)', 'datetime': 'Время'},
              title='MP10')
fig.show()

In [4]:
mp_10 = mp_10[mp_10.index < '2021-01-01']
mp_10['Valor'] = mp_10['Valor'].interpolate(method='polynomial', order=3)
mp_10['Valor'] = pd.to_numeric(mp_10['Valor'])

## Single-option

### Baseline

In [5]:
split_idx = int(len(mp_10['Valor']) * 0.8)
train_ts = mp_10['Valor'].iloc[:split_idx]
test_ts = mp_10['Valor'].iloc[split_idx:]

In [6]:
window_size = 24

def moving_average_forecast(train, test, window):
    predictions = []
    history = list(train)
    for i in range(len(test)):
        if len(history) >= window:
            yhat = np.mean(history[-window:])
        else:
            yhat = np.mean(history)
        predictions.append(yhat)
        history.append(test.iloc[i])
    return predictions

baseline_predictions = moving_average_forecast(train_ts, test_ts, window_size)

In [8]:
window_size = 24
mp_10_ma = mp_10['Valor'].rolling(window=window_size).mean()

fig2 = px.line(title='Временной ряд MP10 со скользящим средним')
fig2.add_scatter(x=mp_10.index, y=mp_10['Valor'].values, mode='lines', name='Original')
fig2.add_scatter(x=mp_10_ma.index, y=mp_10_ma.values, mode='lines', name=f'MA ({window_size}h)')
fig2.update_layout(xaxis_title='Дата', yaxis_title='Значение MP10, ug/m3')
fig2.show()

In [7]:
mae_baseline = mean_absolute_error(test_ts, baseline_predictions)
rmse_baseline = np.sqrt(mean_squared_error(test_ts, baseline_predictions))
print("Baseline (moving_average): MAE =", mae_baseline, "RMSE =", rmse_baseline)

Baseline (moving_average): MAE = 9.564987213745944 RMSE = 12.770337159699759


### FEDOT

In [8]:
forecast_length = len(test_ts)

fedot_model = Fedot(
    problem='ts_forecasting',
    task_params=TsForecastingParams(forecast_length=forecast_length),
    timeout=2
)

fedot_model.fit(np.array(train_ts))
fedot_forecast = fedot_model.predict(features=np.array(train_ts))
fedot_forecast_series = pd.Series(fedot_forecast, index=test_ts.index)

mae_fedot = mean_absolute_error(test_ts, fedot_forecast_series)
rmse_fedot = sqrt(mean_squared_error(test_ts, fedot_forecast_series))
print("FEDOT: MAE =", mae_fedot, "RMSE =", rmse_fedot)

Level 100:root:Topological features operation requires extra dependencies for time series forecasting, which are not installed. It can infuence the performance. Please install it by 'pip install fedot[extra]'


2025-05-01 13:37:26,994 - Topological features operation requires extra dependencies for time series forecasting, which are not installed. It can infuence the performance. Please install it by 'pip install fedot[extra]'


Level 45:root:LaggedTransformationImplementation - Window size of lagged transformation was changed by WindowSizeSelector from 0 to 4176


2025-05-01 13:37:32,380 - LaggedTransformationImplementation - Window size of lagged transformation was changed by WindowSizeSelector from 0 to 4176


Level 45:root:ApiComposer - Initial pipeline was fitted in 167.2 sec.


...

2025-05-01 13:40:20,632 - ApiComposer - Model generation finished


Level 45:root:FEDOT logger - Already fitted initial pipeline is used


2025-05-01 13:40:20,640 - FEDOT logger - Already fitted initial pipeline is used


Level 45:root:FEDOT logger - Final pipeline: {'depth': 2, 'length': 2, 'nodes': [ridge, lagged]}
ridge - {}
lagged - {'window_size': 4176}


2025-05-01 13:40:20,650 - FEDOT logger - Final pipeline: {'depth': 2, 'length': 2, 'nodes': [ridge, lagged]}
ridge - {}
lagged - {'window_size': 4176}
FEDOT: MAE = 11.950453973990088 RMSE = 15.618131255364075


### Comparison

In [11]:
fig_compare = go.Figure()
fig_compare.add_trace(go.Scatter(x=train_ts.index, y=train_ts.values, mode='lines', name='Train Data'))
fig_compare.add_trace(go.Scatter(x=test_ts.index, y=test_ts.values, mode='lines', name='Test Data'))
fig_compare.add_trace(go.Scatter(x=test_ts.index, y=baseline_predictions, mode='lines', name='Baseline (MA)'))
fig_compare.add_trace(go.Scatter(x=test_ts.index, y=fedot_forecast_series.values, mode='lines', name='FEDOT'))
fig_compare.update_layout(title='Forecasting', xaxis_title='Data', yaxis_title='MP10, ug/m3')
fig_compare.show()

# Вывод метрик для обоих методов
metrics_df = pd.DataFrame({
    'Metrics': ['MAE', 'RMSE'],
    'Baseline (MA)': [mae_baseline, rmse_baseline],
    'FEDOT': [mae_fedot, rmse_fedot]
})
print(metrics_df)

  Metrics  Baseline (MA)      FEDOT
0     MAE       9.564987  11.950454
1    RMSE      12.770337  15.618131


## Multivariate

In [96]:
all_polutant_data = data.pivot_table(index='datetime', columns='Poluente', values='Valor')
all_polutant_data = all_polutant_data[all_polutant_data.index < '2016-01-01']
all_polutant_data.head()

Poluente                 CO  MP10  MP2.5    NO   NO2     O3   PTS   SO2
datetime                                                               
2015-01-01 00:30:00  305.53  14.0    8.0  1.69  5.30  30.59  18.0   NaN
2015-01-01 01:30:00  428.31  37.0   10.0  2.28  9.04  28.06  39.0  1.07
2015-01-01 02:30:00  330.15  23.0   22.0  2.35  6.61  30.01  26.0  2.17
2015-01-01 03:30:00  226.61  10.0    8.0  0.64  5.01  31.93  13.0  1.24
2015-01-01 04:30:00  156.58   5.0    5.0  0.51  2.97  35.81   7.0  1.88

In [97]:
all_polutant_data = all_polutant_data.sort_index()
print(all_polutant_data.isna().sum())

Poluente
CO         24
MP10      324
MP2.5     178
NO       7373
NO2      7373
O3         21
PTS       643
SO2       134
dtype: int64


In [98]:
window_size = 5

all_polutant_data_filled = all_polutant_data.copy()

for col in all_polutant_data_filled.columns:
    rolling_mean = all_polutant_data_filled[col].rolling(window=window_size, min_periods=1, center=True).mean()
    all_polutant_data_filled[col] = all_polutant_data_filled[col].fillna(rolling_mean)

In [99]:
all_polutant_data_filled = all_polutant_data_filled[['CO', 'MP10', 'MP2.5', 'O3']]

In [100]:
for column in all_polutant_data_filled.columns:
    fig = px.line(all_polutant_data, y=column, title=f'{column} over time')
    fig.show()

In [103]:
all_polutant_data_filled = all_polutant_data_filled.interpolate(method='polynomial', order=3)

In [104]:
train_size = int(len(all_polutant_data_filled) * 0.8)
train_df, test_df = all_polutant_data_filled.iloc[:train_size], all_polutant_data_filled.iloc[train_size:]
train_target = train_df['MP10']
test_target = test_df['MP10']

### Baseline

In [108]:
ar_model = AutoReg(train_target, lags=24*7, old_names=False).fit()
ar_pred = ar_model.predict(start=len(train_target), end=len(train_target) + len(test_target) - 1, dynamic=False)
ar_pred.index = test_target.index

### FEDOT

In [109]:
forecast_length = len(test_df)
x_train = train_df.drop(columns=['MP10'])
y_train = train_df['MP10']

fedot_model = Fedot(
    problem='ts_forecasting',
    task_params=TsForecastingParams(forecast_length=forecast_length),
    timeout=3
)

fedot_model.fit(features=x_train, target=y_train)
fedot_pred = fedot_model.predict(features=x_train)
fedot_pred_series = pd.Series(fedot_pred, index=test_df.index)

Level 45:root:LaggedTransformationImplementation - Window size of lagged transformation was changed by WindowSizeSelector from 0 to 682


2025-04-30 16:15:34,348 - LaggedTransformationImplementation - Window size of lagged transformation was changed by WindowSizeSelector from 0 to 682


Level 45:root:ApiComposer - Initial pipeline was fitted in 4.0 sec.


2025-04-30 16:15:38,256 - ApiComposer - Initial pipeline was fitted in 4.0 sec.


Level 45:root:ApiComposer - Taking into account n_folds=3, estimated fit time for initial assumption is 11.9 sec.


...

2025-04-30 16:18:37,869 - ApiComposer - Model generation finished


Level 45:root:FEDOT logger - Final pipeline was fitted


2025-04-30 16:18:38,946 - FEDOT logger - Final pipeline was fitted


Level 45:root:FEDOT logger - Final pipeline: {'depth': 2, 'length': 2, 'nodes': [ridge, lagged]}
ridge - {'alpha': 1.5288608905423424}
lagged - {'window_size': 19}


2025-04-30 16:18:38,951 - FEDOT logger - Final pipeline: {'depth': 2, 'length': 2, 'nodes': [ridge, lagged]}
ridge - {'alpha': 1.5288608905423424}
lagged - {'window_size': 19}


### Comparison

In [110]:
def evaluate(y_true, y_pred, name='Model'):
    print(f"🔍 {name} — MAE: {mean_absolute_error(y_true, y_pred):.3f}, "
          f"RMSE: {mean_squared_error(y_true, y_pred, squared=False):.3f}")

evaluate(test_target, ar_pred, 'AutoRegression (baseline)')
evaluate(test_target, fedot_pred_series, 'FEDOT')

fig = go.Figure()
fig.add_trace(go.Scatter(x=test_target.index, y=test_target, name='Actual'))
fig.add_trace(go.Scatter(x=test_target.index, y=ar_pred, name='AutoRegression'))
fig.add_trace(go.Scatter(x=test_target.index, y=fedot_pred_series, name='FEDOT'))
fig.update_layout(title='MP10 Forecast: AutoRegression vs FEDOT vs Actual')
fig.show()

🔍 AutoRegression (baseline) — MAE: 14.204, RMSE: 20.157
🔍 FEDOT — MAE: 13.937, RMSE: 20.201
